<a href="https://colab.research.google.com/github/catarina-moreira/causabilityXAi/blob/master/Diabetes.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Demystifying Predictive Black-Box Models: An Interpretable Probabilistic Approach

Catarina Moreira, Yu-Liang Chou, Mythreyi Velmurugan, Renuka Sindhgatta Rajan, Chun Ouyang, Peter Bruza

**Abstract** 


In [1]:
# Install tensorflow
try:
    # tensorflow_version only exists in Colab
    %tensorflow_version 2.x
except Exception:
    pass

In [2]:
# library to deal with Bayesian Networks
#!pip install pyagrum

In [3]:
import lime
from lime import lime_tabular


In [4]:
# for reproduciability reasons:
import numpy as np
import pandas as pd
import random as rn
import time

%matplotlib inline

# import auxiliary functions
from learning import *

import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


In [5]:
# use only if opening on google colab
#from google.colab import drive
#drive.mount('/content/drive')

## Diabetes Dataset

**Context**
This dataset is originally from the National Institute of Diabetes and Digestive and Kidney Diseases. The objective of the dataset is to diagnostically predict whether or not a patient has diabetes, based on certain diagnostic measurements included in the dataset. Several constraints were placed on the selection of these instances from a larger database. In particular, all patients here are females at least 21 years old of Pima Indian heritage.

**Content**
The datasets consists of several medical predictor variables and one target variable, Outcome. Predictor variables includes the 
- number of pregnancies the patient has had, 
- their BMI, 
- insulin level, 
- age,
- glucose,
- blood pressure,
- skin thickness,
- Diabetes pedigree function


### Checking Dataset

In [6]:
# path to project folder
# please change to your own
PATH = "/Users/catarina/Google Drive/DDS/"

In [7]:
# name of dataset
DATASET_NAME = "diabetes.csv"

# variable containing the class labels in this case the dataset contains:
# 0 - if not diabetes
# 1 - if diabetes
class_var = "Outcome"

# load dataset
dataset_path = PATH + "datasets/" + DATASET_NAME
data = pd.read_csv( dataset_path )

In [8]:
# features
feature_names = data.drop([class_var], axis=1).columns.to_list()

# check how balanced the classes are
data.groupby(class_var).count()

Pregnancies  Glucose  BloodPressure  SkinThickness  Insulin  BMI  \
Outcome                                                                     
0                500      500            500            500      500  500   
1                268      268            268            268      268  268   

         DiabetesPedigreeFunction  Age  
Outcome                                 
0                             500  500  
1                             268  268

### Balanced Dataset

In [9]:
# balance dataset
sampled_data = data.sample(frac=1)
sampled_data = sampled_data[ sampled_data["Outcome"] == 0]
no_data = sampled_data.sample(frac=1)[0:268]

yes_data = data[ data["Outcome"] == 1]

balanced_data = [no_data,yes_data]
balanced_data = pd.concat(balanced_data)

# check how balanced the classes are
balanced_data.groupby(class_var).count()

Pregnancies  Glucose  BloodPressure  SkinThickness  Insulin  BMI  \
Outcome                                                                     
0                268      268            268            268      268  268   
1                268      268            268            268      268  268   

         DiabetesPedigreeFunction  Age  
Outcome                                 
0                             268  268  
1                             268  268

#### Train a Model for the Balanced Dataset

In [10]:
# apply one hot encoder to data
# standardize the input between 0 and 1
X, Y, encoder, scaler = encode_data( balanced_data, class_var)

n_features = X.shape[1]
n_classes = len(balanced_data[class_var].unique())
 
flag = False  # DO NOT CHANGE! Data has already been generated. 
if flag:
    # save training, test and validation data
    generate_save_training_data( dataset_path, X, Y)
    
else:
    # load existing training data
    X_train, Y_train, X_test, Y_test, X_validation, Y_validation= load_training_data( dataset_path )
    

In [11]:
# generate models for grid search
if flag:
    models = grid_search_model_generator( n_features, n_classes )

    # perform grid_search
    HISTORY_DICT = perform_grid_search( models, PATH, DATASET_NAME.replace(".csv",""), 
                                   X_train, Y_train, 
                                   X_validation, Y_validation, X_test, Y_test, 
                                   batch_size=8, epochs=150 )

In [12]:
path_serialisation_model = PATH + "training/" + DATASET_NAME.replace(".csv", "") + "/model/" 
path_serialisation_histr = PATH + "training/" + DATASET_NAME.replace(".csv", "") + "/history/" 

# the best performing model was obtained with 5 hidden layers with 12 neurons each
model_name = "model_h5_N12"
    
if flag:
    
    # get respective model training history and model
    model_history = HISTORY_DICT[ model_name ][0]
    model = HISTORY_DICT[ model_name ][1]

    # save model and model history to file
    save_model_history(  model_history, model_name, path_serialisation_histr )
    save_model( model, model_name, path_serialisation_model )
else:
    model_history = load_model_history( model_name, path_serialisation_histr )
    model = load_model( model_name, path_serialisation_model )
    
model.summary()

Loaded model from disk
Model: "model_h5_N12"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_293 (Dense)            (None, 12)                108       
_________________________________________________________________
dense_294 (Dense)            (None, 12)                156       
_________________________________________________________________
dense_295 (Dense)            (None, 12)                156       
_________________________________________________________________
dense_296 (Dense)            (None, 12)                156       
_________________________________________________________________
dense_297 (Dense)            (None, 12)                156       
_________________________________________________________________
dense_298 (Dense)            (None, 12)                156       
_________________________________________________________________
dense_299 (Dense)            (N

#### Evaluate Model

In [13]:
# evaluate loaded model on test and training data
optim = keras.optimizers.Nadam(lr=0.0001, beta_1=0.9, beta_2=0.999)
model.compile(loss='categorical_crossentropy', optimizer=optim, metrics=['accuracy'])

train_loss, train_acc = model.evaluate(X_train, Y_train, verbose=1)
test_loss, test_acc = model.evaluate(X_test, Y_test, verbose=1)

print('\n[Accuracy] Train: %.3f, Test: %.3f' % (train_acc, test_acc))
print('[Loss] Train: %.3f, Test: %.3f' % (train_loss, test_loss))

80/80 [==============================] - 0s 57us/sample - loss: 0.5311 - accuracy: 0.7375

[Accuracy] Train: 0.759, Test: 0.738
[Loss] Train: 0.496, Test: 0.531


In [14]:
#plot_model_history( model_history, 'Accuracy' )
#plot_model_history( model_history, 'Loss' )


In [15]:
# plot ROC curve
#plot_ROC_Curve( model, X_test, Y_test, n_classes)



### Searching for specific datapoints for local evaluation

In [16]:

local_data_dict = generate_local_predictions( X_test, Y_test, model, scaler, encoder )

# wrapping up information
true_positives = []
true_negatives = []
false_positives = []
false_negatives = []
for instance in local_data_dict:
    
    if( instance['prediction_type'] == 'TRUE POSITIVE'):
        true_positives.append(instance)

    if( instance['prediction_type'] == 'TRUE NEGATIVE' ):
        true_negatives.append(instance)
        
    if( instance['prediction_type'] == 'FALSE POSITIVE' ):
        false_positives.append(instance)
        
    if( instance['prediction_type'] == 'FALSE NEGATIVE' ):
        false_negatives.append(instance)

### Generating Explanations with Bayesian Networks

#### TRUE POSITIVES

In [17]:
label_lst = ["No", "Yes"]
class_var = "Diabetes?"

for instance in true_positives[0:5]:

    # get instance index
    indx = instance['index']
    print("INDEX = " + str(indx))
    
    [bn, inference, infoBN, markov] = generate_BN_explanationsMB(instance, label_lst, feature_names, 
                                                        class_var, encoder, scaler, model, PATH, DATASET_NAME, 
                                                                 variance = 0.25, algorithm="Local Search")
 

INDEX = 0
Selecting Local Search Algorithm


INDEX = 1
Selecting Local Search Algorithm


INDEX = 3
Selecting Local Search Algorithm


INDEX = 7
Selecting Local Search Algorithm


INDEX = 10
Selecting Local Search Algorithm


In [18]:

for instance in true_positives[5:10]:

    # get instance index
    indx = instance['index']
    print("INDEX = " + str(indx))
    
    [bn, inference, infoBN, markov] = generate_BN_explanationsMB(instance, label_lst, feature_names, 
                                                        class_var, encoder, scaler, model, PATH, DATASET_NAME, 
                                                                 variance = 0.25, algorithm="Local Search")
 

INDEX = 14
Selecting Local Search Algorithm


INDEX = 19
Selecting Local Search Algorithm


INDEX = 20
Selecting Local Search Algorithm


INDEX = 31
Selecting Local Search Algorithm


INDEX = 32
Selecting Local Search Algorithm


In [19]:

for instance in true_positives[10:15]:

    # get instance index
    indx = instance['index']
    print("INDEX = " + str(indx))
    
    [bn, inference, infoBN, markov] = generate_BN_explanationsMB(instance, label_lst, feature_names, 
                                                        class_var, encoder, scaler, model, PATH, DATASET_NAME, 
                                                                 variance = 0.25, algorithm="Local Search")
 

INDEX = 35
Selecting Local Search Algorithm


INDEX = 37
Selecting Local Search Algorithm


INDEX = 39
Selecting Local Search Algorithm


INDEX = 41
Selecting Local Search Algorithm


INDEX = 42
Selecting Local Search Algorithm


In [20]:

for instance in true_positives[15:20]:

    # get instance index
    indx = instance['index']
    print("INDEX = " + str(indx))
    
    [bn, inference, infoBN, markov] = generate_BN_explanationsMB(instance, label_lst, feature_names, 
                                                        class_var, encoder, scaler, model, PATH, DATASET_NAME, 
                                                                 variance = 0.25, algorithm="Local Search")

INDEX = 44
Selecting Local Search Algorithm


INDEX = 45
Selecting Local Search Algorithm


INDEX = 47
Selecting Local Search Algorithm


INDEX = 50
Selecting Local Search Algorithm


INDEX = 52
Selecting Local Search Algorithm


In [22]:

for instance in true_positives[20:25]:

    # get instance index
    indx = instance['index']
    print("INDEX = " + str(indx))
    
    [bn, inference, infoBN, markov] = generate_BN_explanationsMB(instance, label_lst, feature_names, 
                                                        class_var, encoder, scaler, model, PATH, DATASET_NAME, 
                                                                 variance = 0.25, algorithm="Local Search")
 

INDEX = 53
Selecting Local Search Algorithm


INDEX = 54
Selecting Local Search Algorithm


INDEX = 61
Selecting Local Search Algorithm


INDEX = 62
Selecting Local Search Algorithm


INDEX = 63
Selecting Local Search Algorithm


In [23]:

for instance in true_positives[25:30]:

    # get instance index
    indx = instance['index']
    print("INDEX = " + str(indx))
    
    [bn, inference, infoBN, markov] = generate_BN_explanationsMB(instance, label_lst, feature_names, 
                                                        class_var, encoder, scaler, model, PATH, DATASET_NAME, 
                                                                 variance = 0.25, algorithm="Local Search")
 

INDEX = 65
Selecting Local Search Algorithm


INDEX = 67
Selecting Local Search Algorithm


INDEX = 68
Selecting Local Search Algorithm


INDEX = 71
Selecting Local Search Algorithm


INDEX = 72
Selecting Local Search Algorithm


In [24]:

for instance in true_positives[30:]:

    # get instance index
    indx = instance['index']
    print("INDEX = " + str(indx))
    
    [bn, inference, infoBN, markov] = generate_BN_explanationsMB(instance, label_lst, feature_names, 
                                                        class_var, encoder, scaler, model, PATH, DATASET_NAME, 
                                                                 variance = 0.25, algorithm="Local Search")
 

INDEX = 74
Selecting Local Search Algorithm


INDEX = 78
Selecting Local Search Algorithm


INDEX = 79
Selecting Local Search Algorithm
